# Cours 3 : Machine Learning - Algorithmes supervisés (1/2)

## Préambule

Les objectifs de cette séance (3h) sont :
* Préparation des bases de modélisation (sampling)
* Mettre en application un modèle supervisé simple.
* Construire un modèle de Machine Learning (cross-validation et hyperparamétrage) pour résoudre un problème de régression
* Analyser les performances du modèle

## Préparation du workspace

### Import de librairies 

In [ ]:
# Données
import numpy as np
import pandas as pd

#Graphiques
import seaborn as sns

sns.set()
import plotly.express as px
import plotly.graph_objects as gp
import sklearn.preprocessing as preproc

#Statistiques
from scipy.stats import chi2_contingency
from sklearn import metrics

# Machine Learning
from sklearn.cluster import KMeans
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import KFold, train_test_split
from sklearn.tree import DecisionTreeClassifier, DecisionTreeRegressor

### Définition des fonctions 

### Constantes

In [24]:
input_path = "./1_inputs"
output_path = "./2_outputs"

### Import des données

In [25]:
path =input_path + '/base_retraitee.csv'
data_retraitee = pd.read_csv(path,sep=",",decimal=".")

## Algorithme supervisé : CART 

Dans cette partie l'objectif est de construire un modèle simple (algorithme CART) afin de voir les différentes étapes nécessaire au lancement d'un modèle
Nous modéliserons directement le coût des sinistres. 

### Construction du modèle

La première étape est de calculer les côut moyen de chaque sinistre (target ou variable réponse). Cette variable sera la variable à prédire en fonction des variables explicatives.

In [26]:
data_model = data_retraitee.copy()

# Filtre pour ne garder que les lignes qui ont un sinistre (NB > 0)
data_model = data_model[data_model['NB'] > 0]

# Calcul du cout moyen "théorique" des sinistres
data_model["CM"] = (data_model["CHARGE"] / data_model["NB"])
data_model = data_model.drop(['CHARGE', 'NB', "EXPO"], axis=1)
data_model.head()

ANNEE_CTR CONTRAT_ANCIENNETE FREQUENCE_PAIEMENT_COTISATION      GROUPE_KM  \
10       2019              (0,1]                       MENSUEL      [0;20000[   
34       2020             (-1,0]                       MENSUEL  [20000;40000[   
36       2019             (-1,0]                       MENSUEL  [20000;40000[   
78       2019             (-1,0]                       MENSUEL  [20000;40000[   
89       2018              (1,2]                       MENSUEL  [20000;40000[   

   ZONE_RISQUE  AGE_ASSURE_PRINCIPAL GENRE  DEUXIEME_CONDUCTEUR  \
10           C                    40     M                False   
34           C                    27     M                 True   
36           L                    19     M                False   
78           B                    40     M                False   
89           C                    20     M                False   

    ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION  ENERGIE EQUIPEMENT_SECURITE  \
10                 37              2017.0  ESSENCE                VRAI   
34                 13              2018.0    AUTRE                FAUX   
36                  2              2017.0  ESSENCE                VRAI   
78                 45              2018.0   DIESEL                FAUX   
89                 11              2014.0  ESSENCE                FAUX   

   VALEUR_DU_BIEN       CM  
10  [15000;20000[  1072.98  
34  [35000;99999[  3750.00  
36      [0;10000[  1838.49  
78  [15000;20000[  4892.74  
89  [25000;35000[   166.73

**Exercice :** construisez les statistiques descriptives de la base utilisée.

In [27]:
data_model.describe(include='all')

ANNEE_CTR CONTRAT_ANCIENNETE FREQUENCE_PAIEMENT_COTISATION  \
count    824.000000                824                           824   
unique          NaN                  5                             3   
top             NaN              (0,1]                       MENSUEL   
freq            NaN                297                           398   
mean    2018.384709                NaN                           NaN   
std        1.515833                NaN                           NaN   
min     2016.000000                NaN                           NaN   
25%     2017.000000                NaN                           NaN   
50%     2018.000000                NaN                           NaN   
75%     2020.000000                NaN                           NaN   
max     2021.000000                NaN                           NaN   

        GROUPE_KM ZONE_RISQUE  AGE_ASSURE_PRINCIPAL GENRE DEUXIEME_CONDUCTEUR  \
count         824         824            824.000000   824                 824   
unique          4          14                   NaN     2                   2   
top     [0;20000[           C                   NaN     M               False   
freq          391         269                   NaN   483                 663   
mean          NaN         NaN             44.383495   NaN                 NaN   
std           NaN         NaN             13.808217   NaN                 NaN   
min           NaN         NaN             19.000000   NaN                 NaN   
25%           NaN         NaN             34.000000   NaN                 NaN   
50%           NaN         NaN             43.000000   NaN                 NaN   
75%           NaN         NaN             53.000000   NaN                 NaN   
max           NaN         NaN             94.000000   NaN                 NaN   

        ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION  ENERGIE EQUIPEMENT_SECURITE  \
count          824.000000          824.000000      824                 824   
unique                NaN                 NaN        3                   2   
top                   NaN                 NaN  ESSENCE                FAUX   
freq                  NaN                 NaN      413                 517   
mean            35.688107         2015.212379      NaN                 NaN   
std             19.370621            3.163782      NaN                 NaN   
min              1.000000         1998.000000      NaN                 NaN   
25%             18.000000         2014.000000      NaN                 NaN   
50%             35.000000         2016.000000      NaN                 NaN   
75%             53.000000         2017.000000      NaN                 NaN   
max             70.000000         2021.000000      NaN                 NaN   

       VALEUR_DU_BIEN            CM  
count             824    824.000000  
unique              6           NaN  
top     [10000;15000[           NaN  
freq              213           NaN  
mean              NaN   4246.016978  
std               NaN   6869.616917  
min               NaN      7.500000  
25%               NaN   1159.961250  
50%               NaN   2541.650000  
75%               NaN   4193.797500  
max               NaN  83421.850000

#### Etude des corrélations parmi les variables explicatives

**Question :** Selon vous, pourquoi faut-il s'intéresser à la corrélation des variables ? 

*Réponse*: Pour avoir un modèle qui fit mieux + déterminer un potentiel effet de causalité entre features et target + sélectionner certaines variables.

In [28]:
data_set = data_model.drop("CM", axis=1)

In [29]:
#Séparation en variables qualitatives ou catégorielles
variables_na = []
variables_numeriques = []
variables_01 = []
variables_categorielles = []
for colu in data_set.columns:
    if True in data_set[colu].isna().unique() :
        variables_na.append(data_set[colu])
    else :
        if str(data_set[colu].dtypes) in ["int32","int64","float64"]:
            if len(data_set[colu].unique())==2 :
                variables_categorielles.append(data_set[colu])
            else :
                variables_numeriques.append(data_set[colu])
        else :
            if len(data_set[colu].unique())==2 :
                variables_categorielles.append(data_set[colu])
            else :
                variables_categorielles.append(data_set[colu])

##### Corrélation des variables catégorielles :

In [16]:
vars_categorielles = pd.DataFrame(variables_categorielles).transpose()

In [31]:
vars_categorielles.head()

CONTRAT_ANCIENNETE FREQUENCE_PAIEMENT_COTISATION      GROUPE_KM  \
10              (0,1]                       MENSUEL      [0;20000[   
34             (-1,0]                       MENSUEL  [20000;40000[   
36             (-1,0]                       MENSUEL  [20000;40000[   
78             (-1,0]                       MENSUEL  [20000;40000[   
89              (1,2]                       MENSUEL  [20000;40000[   

   ZONE_RISQUE GENRE DEUXIEME_CONDUCTEUR  ENERGIE EQUIPEMENT_SECURITE  \
10           C     M               False  ESSENCE                VRAI   
34           C     M                True    AUTRE                FAUX   
36           L     M               False  ESSENCE                VRAI   
78           B     M               False   DIESEL                FAUX   
89           C     M               False  ESSENCE                FAUX   

   VALEUR_DU_BIEN  
10  [15000;20000[  
34  [35000;99999[  
36      [0;10000[  
78  [15000;20000[  
89  [25000;35000[

##### Corrélation des variables numériques :

In [22]:
vars_numeriques = pd.DataFrame(variables_numeriques).transpose()

In [ ]:
# Calcul des corrélations entre variables numériques
correlation_matrix = vars_numeriques.corr()
print("Matrice de corrélation des variables numériques:")
print(correlation_matrix)

fig = px.imshow(
    correlation_matrix, text_auto=True, color_continuous_scale="coolwarm", aspect="auto"
)
fig.update_layout(title="Matrice de corrélation des variables numériques")
fig.show()

Matrice de corrélation des variables numériques:
                      ANNEE_CTR  AGE_ASSURE_PRINCIPAL  ANCIENNETE_PERMIS  \
ANNEE_CTR              1.000000              0.026613           0.040797   
AGE_ASSURE_PRINCIPAL   0.026613              1.000000           0.540899   
ANCIENNETE_PERMIS      0.040797              0.540899           1.000000   
ANNEE_CONSTRUCTION     0.387562             -0.031655           0.033320   

                      ANNEE_CONSTRUCTION  
ANNEE_CTR                       0.387562  
AGE_ASSURE_PRINCIPAL           -0.031655  
ANCIENNETE_PERMIS               0.033320  
ANNEE_CONSTRUCTION              1.000000  


ValueError: 
    Invalid value of type 'builtins.str' received for the 'colorscale' property of imshow
        Received value: 'coolwarm'

    The 'colorscale' property is a colorscale and may be
    specified as:
      - A list of colors that will be spaced evenly to create the colorscale.
        Many predefined colorscale lists are included in the sequential, diverging,
        and cyclical modules in the plotly.colors package.
      - A list of 2-element lists where the first element is the
        normalized color level value (starting at 0 and ending at 1),
        and the second item is a valid color string.
        (e.g. [[0, 'green'], [0.5, 'red'], [1.0, 'rgb(0, 0, 255)']])
      - One of the following named colorscales:
            ['aggrnyl', 'agsunset', 'algae', 'amp', 'armyrose', 'balance',
             'blackbody', 'bluered', 'blues', 'blugrn', 'bluyl', 'brbg',
             'brwnyl', 'bugn', 'bupu', 'burg', 'burgyl', 'cividis', 'curl',
             'darkmint', 'deep', 'de

**Question :** quels sont vos commentaires ?

#### Preprocessing

Deux étapes sont nécessaires avant de lancer l'apprentissage d'un modèle, c'est ce qu'on connait comme le *Preprocessing* :

* Les modèles proposés par la librairie "sklearn" ne gèrent que des variables numériques. Il est donc nécessaire de transformer les variables catégorielles en variables numériques : ce processus s'appelle le *One Hot Encoding*.
* Normaliser les données numériques

**Exercice :** proposez un bout de code permettant de réaliser le One Hot Encoding des variables catégorielles. Vous pourrez utiliser la fonction "preproc.OneHotEncoder" de la librairie sklearn

**Exercice :** proposez un bout de code permettant normaliser les variables numériques présentes dans la base. Vous pourrez utiliser la fonction "preproc.StandardScaler" de la librairie sklearn

#### Sampling

**Exercice :** proposez un bout de code permettant construire la base d'apprentissage (80% des données) et la base de test (20%).

#### Fitting

**Exercice :** proposez un bout de code permettant construire le modèle

**Exercice :** proposez un bout de code permettant d'évaluer les performances du modèle (MAE, MSE et RMSE)

**Question :** que pensez-vous des performances de ce modèle ?

## Algorithme supervisé : Random Forest  

A ce stade, nous avons vu les différentes étapes pour lancer un algorithme de Machine Learning. Néanmoins, ces étapes ne sont pas suffisantes pour construire un modèle performant.  
En effet, afin de construire un modèle performant le Data Scientist doit agir sur l'apprentissage du modèle. Dans ce qui suit nous :
* Changerons d'algorithme pour utiliser un algorithme plus performant (Random Forest)
* Raliserons un *grid search* sur les paramètres du modèle
* Appliquerons l'apprentissage par validation croisée


### Modèle avec Validation Croisée

#### Sampling

#### Fitting avec Cross-Validation

**Exercice :** construisez un modèle RF (RandomForestRegressor) en implémentant la technique de validation croisée. Pensez à enregistrer au sein d'une variable/liste les performances (MAE, MSE & RMSE) du modèle au sein de chaque fold.

In [ ]:
#Initialisation
# Nombre de sous-échantillons pour la cross-validation
num_splits = 5

# Random Forest regressor
rf_regressor = RandomForestRegressor(n_estimators=100, random_state=42)

# Initialisation du KFold cross-validation splitter
kf = KFold(n_splits=num_splits)

# Listes pour enregistrer les performances du modèle
MAE_scores = []
MSE_scores = []
RMSE_scores = []

In [ ]:
# Entrainement avec cross-validation


In [ ]:
# Métriques sur tous les folds

#MAE
for fold, mae in enumerate(MAE_scores, start=1):
    print(f"Fold {fold} MAE:", mae)

In [ ]:
#MSE
for fold, mse in enumerate(MSE_scores, start=1):
    print(f"Fold {fold} MSE:", mse)

In [ ]:
#RMSE
for fold, rmse in enumerate(RMSE_scores, start=1):
    print(f"Fold {fold} RMSE:", rmse)

**Question :** Commentez les résultats.

### Ajout d'un Grid Search pour les hyper paramètres

#### Sampling

#### Fitting avec Cross-Validation et *Grid Search*

**Exercice :** Intégrez la technique de Grid Search pour rechercher les paramètres optimaux du modèle.

In [ ]:
#Initialisation
# Nombre de sous-échantillons pour la cross-validation
num_splits = 5

# Initialisation du KFold cross-validation splitter
kf = KFold(n_splits=num_splits)

# Listes pour enregistrer les performances du modèle
MAE_scores = []
MSE_scores = []
RMSE_scores = []

# Hyperparamètres à tester
n_estimators_values = [] #Complétez ici par les paramètres à tester
max_depth_values = [] #Complétez ici par les paramètres à tester
min_samples_split_values = [] #Complétez ici par les paramètres à tester

# Liste pour sauveagrder les meilleurs résultats
best_score = np.inf
best_params = {}

MAE_best_score = []
MSE_best_score = []
RMSE_best_score = []

In [ ]:
#Complétez ici avec votre code

In [ ]:
# Meilleurs résultats
print("Meilleurs paramètres:", best_params)
print("Meilleure RMSE :", best_score)

In [ ]:
# Métriques sur tous les folds

#RMSE
for fold, rmse in enumerate(RMSE_best_score, start=1):
    print(f"Fold {fold} RMSE:", rmse)


In [ ]:
#MAE
for fold, mse in enumerate(MSE_best_score, start=1):
    print(f"Fold {fold} MSE:", mse)

In [ ]:
#MSE
for fold, mae in enumerate(MAE_best_score, start=1):
    print(f"Fold {fold} MAE:", mae)

**Question :** Commentez les résultats